In [1]:
from platform import python_version

print(python_version())

3.7.10


In [2]:
######################################## Lire les données ########################################################"
import pandas as pd
import scipy

##############################################
VERBOSE_VALUE = 0 # Afficher les logs d'exécution de GridSearch
TEST_SIZE_VALUE = 0.1 # Taux du jeu de données à utiliser dans l'étape de test
CROSS_VALID = 5 # Nombre de K pour la validation croisée
###############################################

data = pd.read_csv("/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/smv2.csv")
### Supprimer toutes les valeurs vides
data = data.fillna(0) 

X = data.drop(["Ecoli","EI","date"],axis=1)
y = data["Ecoli"]

print(X)
print(y)


      station  temperature  conductivite  turbidite  nbjsecappluie  \
0           0         20.6           575       6.70              3   
1           0         22.8           582       6.60              4   
2           0         22.2           582       6.50              5   
3           0         24.3           583       3.20             10   
4           0         25.2           582       0.25             11   
...       ...          ...           ...        ...            ...   
1691        5         24.7           528       3.70              0   
1692        5         23.8           492       5.60              1   
1693        5         21.4           484      15.00              0   
1694        5         19.6           464      18.00              3   
1695        5         19.1           455      14.00              3   

      pluviodujour  pluvioveille  debit  
0              0.0           0.0   24.2  
1              0.0           0.0   20.9  
2              0.0           0.0 

In [3]:

######################################## informations sur les données ########################################################"
print("  * * * * * * * I)  Dataframe information * * * * * * *  ")
print(" 1) Statistics  _  describe ()  ")
print(data.describe())
print("______________________________________")
print(" 2) Informaton (Column, Non-Null, Count, Dtype)  _  info ()  ")
print(data.info())

print("TYPE === ",type(data))


  * * * * * * * I)  Dataframe information * * * * * * *  
 1) Statistics  _  describe ()  
           station          Ecoli             EI  temperature  conductivite  \
count  1696.000000    1696.000000    1696.000000  1696.000000   1696.000000   
mean      8.961085    4337.166274     704.696934    21.770483    537.359080   
std       5.673591   25983.505825    4007.903864     1.585676     56.089111   
min       0.000000      19.000000       8.000000    17.600000    430.000000   
25%       2.000000     425.500000      38.000000    20.600000    488.000000   
50%      10.000000    1014.000000     119.000000    21.875000    525.000000   
75%      14.000000    2781.750000     350.000000    22.900000    590.000000   
max      17.000000  820670.000000  124830.000000    26.500000    657.000000   

         turbidite  nbjsecappluie  pluviodujour  pluvioveille        debit  
count  1696.000000    1696.000000   1696.000000   1696.000000  1696.000000  
mean      7.905596       4.801297      0.96

In [4]:
# Analyse descriptive des données
#! pip install pandas_profiling
from pandas_profiling import ProfileReport
prof = ProfileReport(data, title='Analyse du jeu de la Marne', html={'style':{'full_width':True}})
prof.to_notebook_iframe()

Summarize dataset:   0%|          | 0/24 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
column=["KNN","RF","DT","SVM","Adaboost","Bagging"]
rmse_marne = pd.DataFrame(columns=column)
rmse_seine = pd.DataFrame(columns=column)
mae_marne = pd.DataFrame(columns=column)
mae_seine = pd.DataFrame(columns=column)
rpd_marne = pd.DataFrame(columns=column)
rpd_seine = pd.DataFrame(columns=column)

In [6]:
# Réalisation d'une boucle pour faire les 10 essaye
for i in range(0,10):
    ##############################################################################################"
    ######################################## Split des données  #########################################"
    ##############################################################################################"

    # Diviser les données en entrainement et test
    from sklearn.model_selection import train_test_split
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=TEST_SIZE_VALUE, random_state=i)
    # La division est faite de manière aléatoire en divisant les données en entrainement et en test. 
    # Le random state permet d'avoir une graine pour la reproductibilité. 
    # Le changement de la valeur modifie la division appliquée aux données afin d'obtenir des jeux d'entrainements et de tests différents. 


    # Créer le test de données à exporter
    DataToExport = X_test
    df_Ytest = pd.DataFrame(data=y_test.values, columns=['list'])

    pieces = {'x': DataToExport, 'y': df_Ytest}

    DataToExport = pd.concat(pieces)

    # Imprimer les données à exporter
    print(DataToExport)


    print("  * * * * * * * -- Export -- * * * * * * *  ")
    X_test.to_csv ('data_Test.csv', index = False, header=True, sep=";")
    DataToExport = pd.read_csv("data_Test.csv", sep=";")
    print(type(DataToExport))
    df_Ytest = pd.DataFrame(data=y_test.values)
    DataToExport["Ecolireal"] = df_Ytest
    print("  * * * * * * * -- DATA TEST building -- OK -- * * * * * * *  ")

    ### Standardisation des données

    #La standardisation permet la mise à l'échelle avant l'entraînement. Elle sera effectuée sur les données d'entraînement afin que les modèles n'aient pas accès aux valeurs des données de test.
    #Standardisation par la moyenne : Soustraire la moyenne et diviser par l'écart-type pour chaque caractéristique.


    # Calculer les valeurs de la moyenne et de l'écart-type
    X_train, X_test, y_train, y_test
    train_mean = X_train.mean()
    train_std = X_train.std()
    y_mean = y_train.mean()
    y_std = y_train.std()

    X_train = (X_train - train_mean) / train_std
    X_test = (X_test - train_mean) / train_std
    y_train = (y_train - y_mean) / y_std
    y_test = (y_test - y_mean) / y_std

    # Détermination de l'écart-type après standardisation. 
    import numpy as np
    sd=np.std(y_test)
    print(sd)

    ##### ---------------------- Imports ----------------------------------------------------------------------
    from sklearn.model_selection import GridSearchCV 
    #Créer la grille de paramètres basée sur les résultats de la recherche aléatoire.
    import numpy as np


    ##############################################################################################"
    ######################################## MODEL KNN Split  ####################################"
    ##############################################################################################"


    ## --- Local Params
    modelName = "KNN"
    MethodID = "A"

    print( " ################# ------------- ########################## ")
    print( "Model " ,modelName," is runing ........ !  ")
    from sklearn.neighbors import KNeighborsRegressor
    param_gridKNN = {'n_neighbors': np.arange(1, 30, 2),
                  'weights': ['uniform', 'distance']
             }


    # Sélection du meilleur modèle
    modelKNN =  KNeighborsRegressor()
    best_model_searchKNN = GridSearchCV(estimator = modelKNN, param_grid = param_gridKNN, cv = CROSS_VALID,
                               verbose = VERBOSE_VALUE)
    best_model_searchKNN.fit(X_train,y_train)


    #  Montrer quel est le meilleur modèle
    best_grid = best_model_searchKNN.best_estimator_
    print("  ------------------------------------  ")
    print (MethodID+"-1) BEST Configuration ("+modelName+") is  ==== ",best_grid )
    print("  ------------------------------------  ")


    # prédire les valeurs en utilisant le meilleur modèle
    Y_pred_KNN = best_model_searchKNN.predict(X_test)
    Y=y_test
    num_data = X.shape[0]


    # Erreurs pour l'évaluation des performances
    from sklearn.metrics import mean_squared_error
    from sklearn.metrics import mean_absolute_error
    import math

    mse = mean_squared_error(Y,Y_pred_KNN)
    rmse = math.sqrt(mse)
    rse = math.sqrt(mse/(num_data-2))
    mae=mean_absolute_error(Y,Y_pred_KNN)
    rmse_marne.loc[i,"KNN"]=rmse
    mae_marne.loc[i,"KNN"]=mae
    rpd_marne.loc[i,"KNN"]=sd/rmse
    
    print(MethodID+"-2) Evaluation  "+modelName+" Results : ")
    print("--> RMSE (("+modelName+"))=",rmse)
    print("--> MAE (("+modelName+"))=",mae)
    r = scipy.stats.pearsonr(Y,Y_pred_KNN)
    print("--> Pearson Correlation (("+modelName+"))=",r)


    # Exporter le modèle
    import pickle
    filename = 'bestModel'+modelName+'-pluvio-smv-nrml-Ecoli.pickle'
    pickle.dump(best_model_searchKNN, open(filename, 'wb'))
    print("  ------------------------------------  ")
    print( MethodID+"-3) Model " ,modelName," is generated and exported -- OK --  ")
    print( " ################# ------------- ########################## ")


    # Destandardisation des valeurs prédites
    Y_pred_KNN = (Y_pred_KNN*y_std)+ y_mean
    DataToExport["KNN_Ecoli_pred"] = Y_pred_KNN



    ##############################################################################################"
    ######################################## MODEL RF  Split  ####################################"
    ##############################################################################################"

    from sklearn.ensemble import RandomForestRegressor
    ## --- Local Params
    modelName = "RF"
    MethodID = "B"

    print( " ################# ------------- ########################## ")
    print( "Model " ,modelName," is runing ........ !  ")
    from sklearn.neighbors import KNeighborsRegressor

    param_gridRF = {
        'bootstrap': [True],
        'max_features': [2,3,4,5,6,7,8],
        'n_estimators': [10, 50, 200]
    }


    # Sélection du meilleur modèle
    modelRF =  RandomForestRegressor()
    best_model_searchRF = GridSearchCV(estimator = modelRF, param_grid = param_gridRF, cv = CROSS_VALID,
                               verbose = VERBOSE_VALUE)
    best_model_searchRF.fit(X_train,y_train)


    # Montrer quel est le meilleur modèle
    best_grid = best_model_searchRF.best_estimator_
    print("  ------------------------------------  ")
    print (MethodID+"-1) BEST Configuration ("+modelName+") is  ==== ",best_grid )
    print("  ------------------------------------  ")


    # Prédire les valeurs en utilisant le : best_model
    Y_pred_RF = best_model_searchRF.predict(X_test)
    Y=y_test
    num_data = X.shape[0]


    # Erreurs pour l'évaluation des performances
    from sklearn.metrics import mean_squared_error
    from sklearn.metrics import mean_absolute_error
    import math

    mse = mean_squared_error(Y,Y_pred_RF)
    rmse = math.sqrt(mse)
    rse = math.sqrt(mse/(num_data-2))
    mae=mean_absolute_error(Y,Y_pred_RF)
    rmse_marne.loc[i,"RF"]=rmse
    mae_marne.loc[i,"RF"]=mae
    rpd_marne.loc[i,"RF"]=sd/rmse
    
    print(MethodID+"-2) Evaluation  "+modelName+" Results : ")
    print("--> RMSE (("+modelName+"))=",rmse)
    print("--> MAE (("+modelName+"))=",mae)
    r = scipy.stats.pearsonr(Y,Y_pred_RF)
    print("--> Pearson Correlation (("+modelName+"))=",r)


    # Exporter le modèle
    import pickle
    filename = 'bestModel'+modelName+'-pluvio-smv-nrml-Ecoli.pickle'
    pickle.dump(best_model_searchRF, open(filename, 'wb'))
    print("  ------------------------------------  ")
    print( MethodID+"-3) Model " ,modelName," is generated and exported -- OK --  ")
    print( " ################# ------------- ########################## ")


    # Destandardisation des valeurs prédites
    Y_pred_RF = (Y_pred_RF*y_std)+ y_mean
    DataToExport["RF_Ecoli_pred"] = Y_pred_RF




    ##############################################################################################"
    ######################################## MODEL DT  Split  ####################################"
    ####################################### Arbre de decision ####################################"

    from sklearn.ensemble import RandomForestRegressor
    ## --- Local Params
    modelName = "DT"
    MethodID = "C"

    print( " ################# ------------- ########################## ")
    print( "Model " ,modelName," is runing ........ !  ")
    from sklearn.neighbors import KNeighborsRegressor


    from sklearn import tree
    param_gridDT = {"max_depth": [1, 2, 10, 100],
                  "random_state":[1, 2, 10, 100],
                  "min_samples_leaf":[1, 2, 10, 100]
             }


    # Sélection du meilleur modèle
    modelDT =  tree.DecisionTreeRegressor()
    best_model_searchDT = GridSearchCV(estimator = modelDT, param_grid = param_gridDT, cv = CROSS_VALID,
                               verbose = VERBOSE_VALUE)
    best_model_searchDT.fit(X_train,y_train)


    #  Montrer quel est le meilleur modèle
    best_grid = best_model_searchDT.best_estimator_
    print("  ------------------------------------  ")
    print (MethodID+"-1) BEST Configuration ("+modelName+") is  ==== ",best_grid )
    print("  ------------------------------------  ")


    # Prédire les valeurs en utilisant best_model
    Y_pred_DT = best_model_searchDT.predict(X_test)
    Y=y_test
    num_data = X.shape[0]


    # erreurs pour l'évaluation des performances
    from sklearn.metrics import mean_squared_error
    from sklearn.metrics import mean_absolute_error
    import math

    mse = mean_squared_error(Y,Y_pred_DT)
    rmse = math.sqrt(mse)
    rse = math.sqrt(mse/(num_data-2))
    mae=mean_absolute_error(Y,Y_pred_DT)
    rmse_marne.loc[i,"DT"]=rmse
    mae_marne.loc[i,"DT"]=mae
    rpd_marne.loc[i,"DT"]=sd/rmse
    
    print(MethodID+"-2) Evaluation  "+modelName+" Results : ")
    print("--> RMSE (("+modelName+"))=",rmse)
    print("--> MAE (("+modelName+"))=",mae)
    r = scipy.stats.pearsonr(Y,Y_pred_DT)
    print("--> Pearson Correlation (("+modelName+"))=",r)


    # Exporter le modèle
    import pickle
    filename = 'bestModel'+modelName+'-pluvio-smv-nrml-Ecoli.pickle'
    pickle.dump(best_model_searchDT, open(filename, 'wb'))
    print("  ------------------------------------  ")
    print( MethodID+"-3) Model " ,modelName," is generated and exported -- OK --  ")
    print( " ################# ------------- ########################## ")

    # Déstandardisation des valeurs prédites
    Y_pred_DT = (Y_pred_DT*y_std)+ y_mean
    DataToExport["DT_Ecoli_pred"] = Y_pred_DT



    ##############################################################################################"
    ######################################## MODEL SVM  Split  ####################################"
    ################################ Machine a vecteurs de support  ###############################"
    ######################################### non lineaire ########################################"

    from sklearn.ensemble import RandomForestRegressor
    ## --- Local Params
    modelName = "SVM"
    MethodID = "D"

    print( " ################# ------------- ########################## ")
    print( "Model " ,modelName," is runing ........ !  ")
    from sklearn.neighbors import KNeighborsRegressor


    from sklearn.svm import SVR
    param_gridSVM = {'kernel' : ('sigmoid', 'rbf'),
             'coef0' : [0.01,10,0.5],
             'gamma' : ('auto','scale')
             }


    # Sélection du meilleur modèle
    modelSVM = SVR()
    best_model_searchSVM = GridSearchCV(estimator = modelSVM, param_grid = param_gridSVM, cv = CROSS_VALID,
                             verbose = VERBOSE_VALUE)
    best_model_searchSVM.fit(X_train,y_train)

    #  Show which is the best model
    best_grid = best_model_searchSVM.best_estimator_
    print("  ------------------------------------  ")
    print (MethodID+"-1) BEST Configuration ("+modelName+") is  ==== ",best_grid )
    print("  ------------------------------------  ")


    #  Montrer quel est le meilleur modèle
    Y_pred_SVM = best_model_searchSVM.predict(X_test)
    Y=y_test
    num_data = X.shape[0]


    # Prédire les valeurs en utilisant best_model
    from sklearn.metrics import mean_squared_error
    from sklearn.metrics import mean_absolute_error
    import math

    mse = mean_squared_error(Y,Y_pred_SVM)
    rmse = math.sqrt(mse)
    rse = math.sqrt(mse/(num_data-2))
    mae=mean_absolute_error(Y,Y_pred_SVM)
    rmse_marne.loc[i,"SVM"]=rmse
    mae_marne.loc[i,"SVM"]=mae
    rpd_marne.loc[i,"SVM"]=sd/rmse
    
    print(MethodID+"-2) Evaluation  "+modelName+" Results : ")
    print("--> RMSE (("+modelName+"))=",rmse)
    print("--> MAE (("+modelName+"))=",mae)
    r = scipy.stats.pearsonr(Y,Y_pred_SVM)
    print("--> Pearson Correlation (("+modelName+"))=",r)


    # Export the model
    import pickle
    filename = 'bestModel'+modelName+'-pluvio-smv-nrml-Ecoli.pickle'
    pickle.dump(best_model_searchSVM, open(filename, 'wb'))
    print("  ------------------------------------  ")
    print( MethodID+"-3) Model " ,modelName," is generated and exported -- OK --  ")
    print( " ################# ------------- ########################## ")


    # Destandardisation des valeurs prédites 
    Y_pred_SVM = (Y_pred_SVM*y_std)+ y_mean
    DataToExport["SVM_Ecoli_pred"] = Y_pred_SVM



    ##############################################################################################"
    ######################################## MODEL AdaBoost  Split  ####################################"
    ##############################################################################################"

    from sklearn.ensemble import RandomForestRegressor
    ## --- Local Params
    modelName = "AdaBoost"
    MethodID = "E"

    print( " ################# ------------- ########################## ")
    print( "Model " ,modelName," is runing ........ !  ")


    from sklearn.ensemble import AdaBoostRegressor
    param_gridADaBoost = {'base_estimator__min_samples_leaf':[1,2, 5],
                  "learning_rate": [0.2,0.5],
                  "n_estimators": [20, 50, 100]
             }


    # Sélection du meilleur modèle
    from sklearn import tree
    DTC = tree.DecisionTreeRegressor(random_state = 11, max_features = "auto",
                                     max_depth = None)
    ModelAdaBoostDTC = AdaBoostRegressor(base_estimator = DTC)
    best_model_searchAdaBoost = GridSearchCV(estimator = ModelAdaBoostDTC, param_grid = param_gridADaBoost, cv = CROSS_VALID,
                               verbose = VERBOSE_VALUE)
    best_model_searchAdaBoost.fit(X_train,y_train)


    #  Montrer quel est le meilleur modèle
    best_grid = best_model_searchAdaBoost.best_estimator_
    print("  ------------------------------------  ")
    print (MethodID+"-1) BEST Configuration ("+modelName+") is  ==== ",best_grid )
    print("  ------------------------------------  ")


    # Prédire les valeurs en utilisant best_model
    Y_pred_AdaBoost = best_model_searchAdaBoost.predict(X_test)
    Y=y_test
    num_data = X.shape[0]


    # Erreurs pour l'évaluation des performances
    from sklearn.metrics import mean_squared_error
    from sklearn.metrics import mean_absolute_error
    import math

    mse = mean_squared_error(Y,Y_pred_AdaBoost)
    rmse = math.sqrt(mse)
    rse = math.sqrt(mse/(num_data-2))
    mae=mean_absolute_error(Y,Y_pred_AdaBoost)
    rmse_marne.loc[i,"Adaboost"]=rmse
    mae_marne.loc[i,"Adaboost"]=mae
    rpd_marne.loc[i,"Adaboost"]=sd/rmse
    
    print(MethodID+"-2) Evaluation  "+modelName+" Results : ")
    print("--> RMSE (("+modelName+"))=",rmse)
    print("--> MAE (("+modelName+"))=",mae)
    r = scipy.stats.pearsonr(Y,Y_pred_AdaBoost)
    print("--> Pearson Correlation (("+modelName+"))=",r)


    # Exportez le modèle
    import pickle
    filename = 'bestModel'+modelName+'-pluvio-smv-nrml-Ecoli.pickle'
    pickle.dump(best_model_searchAdaBoost, open(filename, 'wb'))
    print("  ------------------------------------  ")
    print( MethodID+"-3) Model " ,modelName," is generated and exported -- OK --  ")
    print( " ################# ------------- ########################## ")


    # Destandardisation des valeurs prédites 
    Y_pred_AdaBoost = (Y_pred_AdaBoost*y_std)+ y_mean
    DataToExport["AdaBoost_Ecoli_pred"] = Y_pred_AdaBoost


    ##############################################################################################"
    ######################################## MODEL Bagging avec estimator RF ####################################"
    ##############################################################################################"

    from sklearn.ensemble import RandomForestRegressor
    ## --- Local Params
    modelName = "BaggingRF"
    MethodID = "H"

    print( " ################# ------------- ########################## ")
    print( "Model " ,modelName," is runing ........ !  ")


    from sklearn.ensemble import BaggingRegressor
    from sklearn.datasets import make_regression
    X_b, y_b = make_regression(n_samples=100, n_features=8,n_informative=2, n_targets=1, random_state=0, shuffle=False)

    param_gridBag = {
        'bootstrap': [True],
        'max_features': [0, 8],
        'n_estimators': [10, 50, 200]
    }


    # Sélection du meilleur modèle
    modelRF =  RandomForestRegressor()
    modelBaggingRF = BaggingRegressor(base_estimator=modelRF, n_estimators=10, random_state=0).fit(X_b, y_b) # base estimator par defaut DesicionTreeRegressor

    best_model_searchBag2 = GridSearchCV(estimator = modelBaggingRF, param_grid = param_gridBag, cv = CROSS_VALID,
                               verbose = VERBOSE_VALUE)
    best_model_searchBag2.fit(X_train,y_train)


    #  Montrer quel est le meilleur modèle
    best_grid = best_model_searchBag2.best_estimator_
    print("  ------------------------------------  ")
    print (MethodID+"-1) BEST Configuration ("+modelName+") is  ==== ",best_grid )
    print("  ------------------------------------  ")


    # Prédire les valeurs en utilisant best_model
    Y_pred_Bag2 = best_model_searchBag2.predict(X_test)
    Y=y_test
    num_data = X.shape[0]


    # Erreurs pour l'évaluation des performances
    from sklearn.metrics import mean_squared_error
    from sklearn.metrics import mean_absolute_error
    import math

    mse = mean_squared_error(Y,Y_pred_Bag2)
    rmse = math.sqrt(mse)
    rse = math.sqrt(mse/(num_data-2))
    mae=mean_absolute_error(Y,Y_pred_Bag2)
    rmse_marne.loc[i,"Bagging"]=rmse
    mae_marne.loc[i,"Bagging"]=mae
    rpd_marne.loc[i,"Bagging"]=sd/rmse
    
    print(MethodID+"-2) Evaluation  "+modelName+" Results : ")
    print("--> RMSE (("+modelName+"))=",rmse)
    print("--> MAE (("+modelName+"))=",mae)
    r = scipy.stats.pearsonr(Y,Y_pred_Bag2)
    print("--> Pearson Correlation (("+modelName+"))=",r)


    # Exportez le modèle
    import pickle
    filename = 'bestModel'+modelName+'-pluvio-smv-nrml-Ecoli.pickle'
    pickle.dump(best_model_searchBag2, open(filename, 'wb'))
    print("  ------------------------------------  ")
    print( MethodID+"-3) Model " ,modelName," is generated and exported -- OK --  ")
    print( " ################# ------------- ########################## ")

    # Destandardisation des valeurs prédites
    Y_pred_Bag2 = (Y_pred_Bag2*y_std)+ y_mean
    DataToExport["Bagging_Ecoli_pred"] = Y_pred_Bag2




    ######################################## prédictions pour la Seine ########################################################"

    # Lire les données de la Seine
    data2 = pd.read_csv("/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/seine.csv")
    X_test2 = data2.drop(["Ecoli","EI","date"],axis=1)
    y_test2 = data2["Ecoli"]

    # Standardisation des données de la seine 
    X_test2 = (X_test2 - train_mean) / train_std
    y_test2 = (y_test2 - y_mean) / y_std

    # Détermination de l'écart-type sur les données de la Seine. 
    sd=np.std(y_test2)
    print(sd)

    # Importé les différents modèles générés précédemment
    import pickle
    loaded_model_knn=pickle.load(open('bestModelKNN-pluvio-smv-nrml-Ecoli.pickle', 'rb'))
    loaded_model_rf=pickle.load(open('bestModelRF-pluvio-smv-nrml-Ecoli.pickle', 'rb'))
    loaded_model_dt=pickle.load(open('bestModelDT-pluvio-smv-nrml-Ecoli.pickle', 'rb'))
    loaded_model_svm=pickle.load(open('bestModelSVM-pluvio-smv-nrml-Ecoli.pickle', 'rb'))
    loaded_model_adaboost=pickle.load(open('bestModelAdaBoost-pluvio-smv-nrml-Ecoli.pickle', 'rb'))
    loaded_model_bagging=pickle.load(open('bestModelBaggingRF-pluvio-smv-nrml-Ecoli.pickle', 'rb'))


    ### Prédiction avec le modèle KNN
    Y_pred_KNN = loaded_model_knn.predict(X_test2)

    # Erreurs pour l'évaluation des performances
    mse = mean_squared_error(y_test2,Y_pred_KNN)
    rmse = math.sqrt(mse)
    print('knn')
    print("--> RMSE knn=",rmse)
    mae=mean_absolute_error(y_test2,Y_pred_KNN)
    print("--> MAE knn=",mae)
    r = scipy.stats.pearsonr(y_test2,Y_pred_KNN)
    print("--> Pearson Correlation knn=",r)

    rmse_seine.loc[i,"KNN"]=rmse
    mae_seine.loc[i,"KNN"]=mae
    rpd_seine.loc[i,"KNN"]=sd/rmse
    
    # Destandardisation des valeurs prédites
    Y_pred_KNN = (Y_pred_KNN*y_std)+ y_mean
    data2["knn"] = Y_pred_KNN


    ### Prédiction avec le modèle RF
    Y_pred_rf = loaded_model_rf.predict(X_test2)

    # Erreurs pour l'évaluation des performances
    mse = mean_squared_error(y_test2,Y_pred_rf)
    rmse = math.sqrt(mse)
    print('rf')
    print("--> RMSE rf=",rmse)
    mae=mean_absolute_error(y_test2,Y_pred_rf)
    print("--> MAE rf=",mae)
    r = scipy.stats.pearsonr(y_test2,Y_pred_rf)
    print("--> Pearson Correlation rf=",r)

    rmse_seine.loc[i,"RF"]=rmse
    mae_seine.loc[i,"RF"]=mae
    rpd_seine.loc[i,"RF"]=sd/rmse
    
    # Destandardisation des valeurs prédites
    Y_pred_rf = (Y_pred_rf*y_std)+ y_mean
    data2["rf"] = Y_pred_rf


    ### Prédiction avec le modèle DT
    Y_pred_dt = loaded_model_dt.predict(X_test2)

    # Erreurs pour l'évaluation des performances
    mse = mean_squared_error(y_test2,Y_pred_dt)
    rmse = math.sqrt(mse)
    print('dt')
    print("--> RMSE dt=",rmse)
    mae=mean_absolute_error(y_test2,Y_pred_dt)
    print("--> MAE dt=",mae)
    r = scipy.stats.pearsonr(y_test2,Y_pred_dt)
    print("--> Pearson Correlation dt=",r)
    rmse_seine.loc[i,"DT"]=rmse
    mae_seine.loc[i,"DT"]=mae
    rpd_seine.loc[i,"DT"]=sd/rmse
    
    # Destandardisation des valeurs prédites
    Y_pred_dt = (Y_pred_dt*y_std)+ y_mean
    data2["dt"] = Y_pred_dt


    ### Prédiction avec le modèle SVM
    Y_pred_svm = loaded_model_svm.predict(X_test2)

    # Erreurs pour l'évaluation des performances
    mse = mean_squared_error(y_test2,Y_pred_svm)
    rmse = math.sqrt(mse)
    print('svm')
    print("--> RMSE svm =",rmse)
    mae=mean_absolute_error(y_test2,Y_pred_svm)
    print("--> MAE svm=",mae)
    r = scipy.stats.pearsonr(y_test2,Y_pred_svm)
    print("--> Pearson Correlation svm=",r)

    rmse_seine.loc[i,"SVM"]=rmse
    mae_seine.loc[i,"SVM"]=mae
    rpd_seine.loc[i,"SVM"]=sd/rmse
    
    # Destandardisation des valeurs prédites
    Y_pred_svm = (Y_pred_svm*y_std)+ y_mean
    data2["svm"] = Y_pred_svm


    ### Prédiction avec le modèle AdaBoost
    Y_pred_adaboost = loaded_model_adaboost.predict(X_test2)

    # Erreurs pour l'évaluation des performances
    mse = mean_squared_error(y_test2,Y_pred_adaboost)
    rmse = math.sqrt(mse)
    print('adaboost')
    print("--> RMSE  adaboost =",rmse)
    mae=mean_absolute_error(y_test2,Y_pred_adaboost)
    print("--> MAE adaboost=",mae)
    r = scipy.stats.pearsonr(y_test2,Y_pred_adaboost)
    print("--> Pearson Correlation adaboost=",r)
    rmse_seine.loc[i,"Adaboost"]=rmse
    mae_seine.loc[i,"Adaboost"]=mae
    rpd_seine.loc[i,"Adaboost"]=sd/rmse
    
    # Destandardisation des valeurs prédites
    Y_pred_adaboost = (Y_pred_adaboost*y_std)+ y_mean
    data2["adaboost"] = Y_pred_adaboost


    ### Prédiction avec le modèle Bagging
    Y_pred_bagging = loaded_model_bagging.predict(X_test2)

    # Erreurs pour l'évaluation des performances
    mse = mean_squared_error(y_test2,Y_pred_bagging)
    rmse = math.sqrt(mse)
    print('adaboost')
    print("--> RMSE  bagging =",rmse)
    mae=mean_absolute_error(y_test2,Y_pred_bagging)
    print("--> MAE bagging=",mae)
    r = scipy.stats.pearsonr(y_test2,Y_pred_bagging)
    print("--> Pearson Correlation bagging=",r)
    rmse_seine.loc[i,"Bagging"]=rmse
    mae_seine.loc[i,"Bagging"]=mae
    rpd_seine.loc[i,"Bagging"]=sd/rmse
    
    # Destandardisation des valeurs prédites
    Y_pred_bagging = (Y_pred_bagging*y_std)+ y_mean
    data2["bagging"] = Y_pred_bagging

    ######################################## Exporter les données   ####################################"

    # Exporter les données avec les valeurs de prédiction pour tous les modèles 
    print( " ======================================================= ")
    print( " ======================================================= ")

    print("  * * * * * * * IV) Export CSV  * * * * * * *  ")
    DataToExport.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/data_prediValuesML_ecoli_smv_seed'+str(i)+'.csv', index = False, header=True, sep=";")
    data2.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/data_prediValuesML_ecoli_vdp_seed'+str(i)+'.csv', index = False, header=True, sep=";")


        station  temperature  conductivite  turbidite  nbjsecappluie  \
x 1018     13.0        21.90         532.0        6.3            2.0   
  6         0.0        24.30         585.0        4.6           16.0   
  107       1.0        24.04         582.0        2.3           17.0   
  34        0.0        21.83         495.0        5.8            2.0   
  1685      5.0        21.20         624.0        4.8            2.0   
...         ...          ...           ...        ...            ...   
y 165       NaN          NaN           NaN        NaN            NaN   
  166       NaN          NaN           NaN        NaN            NaN   
  167       NaN          NaN           NaN        NaN            NaN   
  168       NaN          NaN           NaN        NaN            NaN   
  169       NaN          NaN           NaN        NaN            NaN   

        pluviodujour  pluvioveille  debit    list  
x 1018           0.0           0.0  37.19     NaN  
  6              0.0           

/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:619: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/ensemble/_bagging.py", line 244, in fit
    return self._fit(X, y, self.max_samples, sample_weight=sample_weight)
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/ensemble/_bagging.py", line 321, in _fit
    raise ValueError("max_features must be in (0, n_features]")
ValueError: max_features must be in (0, n_features]

  FitFailedWarning)
/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:619: F

/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_search.py:925: UserWarning: One or more of the test scores are non-finite: [        nan         nan         nan -3.31051516 -2.08456474 -2.39930328]
  category=UserWarning


  ------------------------------------  
H-1) BEST Configuration (BaggingRF) is  ====  BaggingRegressor(base_estimator=RandomForestRegressor(), max_features=8,
                 n_estimators=50, random_state=0)
  ------------------------------------  
H-2) Evaluation  BaggingRF Results : 
--> RMSE ((BaggingRF))= 0.3057169447375185
--> MAE ((BaggingRF))= 0.11587941637683544
--> Pearson Correlation ((BaggingRF))= (0.48708606316411623, 1.6335899274042814e-11)
  ------------------------------------  
H-3) Model  BaggingRF  is generated and exported -- OK --  
 ################# ------------- ########################## 
0.2560126927865768
knn
--> RMSE knn= 0.2867677147778282
--> MAE knn= 0.22532226098880997
--> Pearson Correlation knn= (0.01824697530634862, 0.5673243650252392)
rf
--> RMSE rf= 0.33080880709223637
--> MAE rf= 0.2353725221502402
--> Pearson Correlation rf= (0.3288017315542668, 2.9034688634924676e-26)
dt
--> RMSE dt= 0.2993732509971782
--> MAE dt= 0.26714783837437966
--> Pearson

/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:619: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/ensemble/_bagging.py", line 244, in fit
    return self._fit(X, y, self.max_samples, sample_weight=sample_weight)
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/ensemble/_bagging.py", line 321, in _fit
    raise ValueError("max_features must be in (0, n_features]")
ValueError: max_features must be in (0, n_features]

  FitFailedWarning)
/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:619: F

...

/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_search.py:925: UserWarning: One or more of the test scores are non-finite: [        nan         nan         nan -1.36277665 -0.90896269 -0.81532648]
  category=UserWarning


  ------------------------------------  
H-1) BEST Configuration (BaggingRF) is  ====  BaggingRegressor(base_estimator=RandomForestRegressor(), max_features=8,
                 n_estimators=200, random_state=0)
  ------------------------------------  
H-2) Evaluation  BaggingRF Results : 
--> RMSE ((BaggingRF))= 0.78963671422814
--> MAE ((BaggingRF))= 0.173207552225717
--> Pearson Correlation ((BaggingRF))= (0.34804231804739594, 3.308530145379323e-06)
  ------------------------------------  
H-3) Model  BaggingRF  is generated and exported -- OK --  
 ################# ------------- ########################## 
0.26469982367252604
knn
--> RMSE knn= 0.30186324328198366
--> MAE knn= 0.24461638824966728
--> Pearson Correlation knn= (0.052625798267013205, 0.09880146455164264)
rf
--> RMSE rf= 0.3205022133811777
--> MAE rf= 0.24300706144291756
--> Pearson Correlation rf= (0.2841761575011166, 9.403791027081675e-20)
dt
--> RMSE dt= 0.34412019041940595
--> MAE dt= 0.2752305712505489
--> Pearson 

/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:619: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/ensemble/_bagging.py", line 244, in fit
    return self._fit(X, y, self.max_samples, sample_weight=sample_weight)
  File "/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/ensemble/_bagging.py", line 321, in _fit
    raise ValueError("max_features must be in (0, n_features]")
ValueError: max_features must be in (0, n_features]

  FitFailedWarning)
/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_validation.py:619: F

/home/manel/anaconda3/envs/tf2/lib/python3.7/site-packages/sklearn/model_selection/_search.py:925: UserWarning: One or more of the test scores are non-finite: [        nan         nan         nan -1.30369607 -0.8107232  -0.69837481]
  category=UserWarning


  ------------------------------------  
H-1) BEST Configuration (BaggingRF) is  ====  BaggingRegressor(base_estimator=RandomForestRegressor(), max_features=8,
                 n_estimators=200, random_state=0)
  ------------------------------------  
H-2) Evaluation  BaggingRF Results : 
--> RMSE ((BaggingRF))= 0.4116417132094686
--> MAE ((BaggingRF))= 0.12760653949242617
--> Pearson Correlation ((BaggingRF))= (0.4421300967866665, 1.5786243940496074e-09)
  ------------------------------------  
H-3) Model  BaggingRF  is generated and exported -- OK --  
 ################# ------------- ########################## 
0.255702562973376
knn
--> RMSE knn= 0.27171506701696063
--> MAE knn= 0.20176919697809723
--> Pearson Correlation knn= (0.09284621298487482, 0.003539222954227253)
rf
--> RMSE rf= 0.299310615125345
--> MAE rf= 0.21889442150763286
--> Pearson Correlation rf= (0.41758516475138374, 7.601431262009779e-43)
dt
--> RMSE dt= 0.29784397882451563
--> MAE dt= 0.26249448672685494
--> Pears

In [7]:
######################################## Exporter les mesures   ####################################"
rmse_marne.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/rmse_marne.csv', index = False, header=True, sep=";")
rmse_seine.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/rmse_seine.csv', index = False, header=True, sep=";")
mae_marne.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/mae_marne.csv', index = False, header=True, sep=";")
mae_seine.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/mae_seine.csv', index = False, header=True, sep=";")
rpd_marne.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/rpd_marne.csv', index = False, header=True, sep=";")
rpd_seine.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/rpd_seine.csv', index = False, header=True, sep=";")

In [8]:
rmse_seine.to_csv ('/home/manel/Bureau/BD/donnee+pluvio/smv+vdp-pluvio/donnee-sans-na/smv-vdp/ML/train_smv/rmse_seine.csv', index = False, header=True, sep=";")


In [9]:
rmse_marne

KNN        RF        DT       SVM  Adaboost   Bagging
0   0.30433  0.309341  0.322389  0.249791  0.291783  0.305717
1  0.441506  0.399193  0.444259  0.425926  0.294036  0.452147
2  1.690229  1.685799  1.663401  1.695827  1.368765  1.664524
3  0.288241  0.275484  0.276943  0.251888  0.233751  0.367132
4  0.344096  0.334465  0.457242  0.332677  0.442949  0.399508
5  0.839827  0.795672  0.831745  0.820329  0.717924    0.7086
6   0.94413   0.77295  0.852797  0.836069  0.779464  0.779831
7  0.346336  0.316677  0.342469   0.32585  0.279304  0.455898
8    0.8259  0.794656  0.817302  0.798761  0.752785  0.789637
9  0.229703  0.205092  0.324744  0.181968  0.137764  0.411642

In [10]:
##############################################################################################"
################################### Analyser le modèle RF  ####################################"
##############################################################################################"

#! pip install treeinterpreter
from treeinterpreter import treeinterpreter as ti

rf = RandomForestRegressor(max_features=8, n_estimators=200)
rf.fit(X_train,y_train)

prediction, bias, contributions = ti.predict(rf, X_test)


In [11]:
prediction, bias, contributions

(array([[ 1.54468030e-01],
        [-2.32673731e-03],
        [-1.51571643e-01],
        [-8.59557146e-02],
        [ 4.04479371e-02],
        [-1.28296887e-01],
        [-7.45715177e-02],
        [ 7.22034482e-01],
        [-1.02763085e-01],
        [-1.28589611e-01],
        [-8.39200109e-02],
        [-5.80605329e-02],
        [-1.14763302e-01],
        [ 3.75690274e-02],
        [-1.09923929e-01],
        [ 2.06424808e-02],
        [ 4.53147701e-02],
        [-1.31817812e-01],
        [-1.01896812e-01],
        [-1.06366390e-01],
        [-7.56849305e-02],
        [ 1.51443765e-01],
        [-1.36066245e-01],
        [-1.38468449e-01],
        [ 6.33391687e-02],
        [-1.28269060e-01],
        [ 2.25090472e-01],
        [ 6.23914497e-03],
        [ 1.64750530e-01],
        [-3.37662585e-03],
        [-1.27149057e-01],
        [-1.40817929e-01],
        [ 5.69104806e-01],
        [-1.25218068e-01],
        [-1.23575043e-01],
        [-1.82581324e-02],
        [-1.52752406e-02],
 